In [ ]:
# install git for windows first
"""https://gitforwindows.org/"""
print('Install manually git for windows for the following code to work on windows')

#install libraries
!pip install numpy
!pip install pandas
!pip install datetime
!pip install bokeh
!pip install requests
!pip install xml
!pip install operator

# Install QC library
!pip install git+git://github.com/ioos/ioos_qc.git

# # Alternative installation (install specific branch):
""" !pip uninstall -y ioos_qc"""
""" !pip install git+git://github.com/ioos/ioos_qc.git@BRANCHNAME"""

# # Alternative installation (run with local updates):
""" !pip uninstall -y ioos_qc"""
""" import sys"""
""" sys.path.append(str(libdir))"""

In [1]:
# Setup directories
from pathlib import Path
basedir = Path().absolute()
libdir = basedir.parent.parent.parent
print(basedir,libdir)

# Other imports
import pandas as pd
import numpy as np
import numpy.ma as ma
import requests
import operator

from datetime import datetime
#fast parser https://stackoverflow.com/questions/1912434/how-do-i-parse-xml-in-python
import xml.etree.ElementTree as ET

from bokeh.layouts import gridplot
from bokeh.plotting import figure, show, output_file, output_notebook
output_notebook()

C:\Users\karunakar.kintada\Documents\pyNotebooks\HawQi C:\Users\karunakar.kintada


Loading BokehJS ...

In [2]:
#Get Qartod
from ioos_qc.config import QcConfig
from ioos_qc import qartod

In [3]:
# Method to plot QC results using Bokeh
def plot_results(data, var_name, results, title, test_name):

    time = data['timestamp']
    obs = data[var_name]
    qc_test = results['qartod'][test_name]

    qc_pass = np.ma.masked_where(qc_test != 1, obs)
    qc_suspect = np.ma.masked_where(qc_test != 3, obs)
    qc_fail = np.ma.masked_where(qc_test != 4, obs)
    qc_notrun = np.ma.masked_where(qc_test != 2, obs)

    p1 = figure(x_axis_type="datetime", title=test_name + ' : ' + title)
    p1.grid.grid_line_alpha=0.3
    p1.xaxis.axis_label = 'Time'
    p1.yaxis.axis_label = 'Observation Value'

    p1.line(time, obs,  legend_label='obs', color='#A6CEE3')
    p1.circle(time, qc_notrun, size=2, legend_label='qc not run', color='gray', alpha=0.2)
    p1.circle(time, qc_pass, size=4, legend_label='qc pass', color='green', alpha=0.5)
    p1.circle(time, qc_suspect, size=4, legend_label='qc suspect', color='orange', alpha=0.7)
    p1.circle(time, qc_fail, size=6, legend_label='qc fail', color='red', alpha=1.0)

    #output_file("qc.html", title="qc example")

    show(gridplot([[p1]], plot_width=800, plot_height=400))


"""
#there is some issue with the hilltop package time format against pandas requirements, so ignoring at the moment
"""
import Hilltop

dfile1 = Hilltop.Connect("N:\HilltopData\Hydro_Working\Hawqi AutoProcessing\Hawqi_Raw.hts")
sites = Hilltop.SiteList(dfile1)
print(sites)

#cant use at the moment as it has issues with the time format _convert_listlike_datetimes in pandas\core\tools\datetimes.py
#ValueError: cannot specify both format and unit

#first try || not iterating through sites at the moment
measurements = Hilltop.MeasurementList(dfile1,sites[0])
#print(measurements)
data = Hilltop.GetData(dfile1, sites[0], 'Air Temperature','1-jan-2015','1-jan-2020') #throwing error

In [4]:
#Hilltop connector
"""Using emar api instead"""

#what observation are we processing
measurementName = "Temperature 5m" #you should have an idea of what you are querying
measNameEqQartod = ""
startDate = '1-jan-2015' 
endDate   = '1-jan-2020'
reqInterval = '1 hour'
reqMethod = 'Average'

#apiRoot = "https://data.hbrc.govt.nz/Envirodata/EMAR.hts?Service=Hilltop"
##https://data.hbrc.govt.nz/EnviroData/Telemetry.hts?service=Hilltop&request=GetData&Site=HAWQi&Measurement=Temperature%205m&From=1/12/2017&To=1/1/2020
apiRoot="https://data.hbrc.govt.nz/EnviroData/Telemetry.hts?service=Hilltop"

#get all the sites for requisite measurement type
requestType = "SiteList"
myWebRequest =  apiRoot + '&Request='+requestType+ '&Measurement='+measurementName
#print(myWebRequest)
r = requests.get(myWebRequest)
#print(r.text)
sites = []
root = ET.fromstring(r.content)
for child in root.iter('*'):
    #print(child.tag,child.attrib)
    if child.tag == 'Site':
        sites.append(child.attrib['Name'])
print('sites: ',sites)

timeList = []
obsList = []
#get the observation data for each site
requestType = "GetData"
# we will iterate through more sites later.
site = sites[0]
#https://data.hbrc.govt.nz/Envirodata/EMAR.hts?Service=Hilltop&Request=GetData&Site=Ngaruroro%20River%20at%20Fernhill&Measurement=Flow%20[Water%20Level]&From=2014-01-01&To=2015-12-01&Interval=1%20hour&method=Average'
myWebRequest =  apiRoot + '&Request='+requestType+'&Site='+site+'&Measurement='+measurementName+'&From='+startDate+'&To='+endDate
#...+'&Interval='+reqInterval+'&method='+reqMethod
#print(myWebRequest)
r = requests.get(myWebRequest)
#print(r.text)
root = ET.fromstring(r.content)
for child in root.iter('E'):
    #print(child.tag,child.attrib)
    for miter in child.iter('*'):
        #print(miter.tag,miter.text)
        if miter.tag == 'T':
            timeList.append(np.datetime64(datetime.strptime(miter.text,'%Y-%m-%dT%H:%M:%S')))#.timestamp()))
            #timeList.append(datetime.strptime(miter.text,'%Y-%m-%dT%H:%M:%S').timestamp())
        if miter.tag == 'I1':
            obsList.append(miter.text)
            
df={'timestamp':np.array(timeList), measurementName:np.array(obsList)}
#print(data)
data = pd.DataFrame (df, columns = ['timestamp',measurementName])
data.head()


#print(hasattr(df['timestamp'], 'dtype'))
#print(np.issubdtype(df['timestamp'].dtype, np.datetime64))

sites:  ['HAWQi', 'Lake Tutira Buoy', 'Lake Waikopiro Buoy']


timestamp Temperature 5m
0 2015-01-01 13:10:04        18.6133
1 2015-01-01 14:09:07        18.4373
2 2015-01-01 15:09:36        18.3116
3 2015-01-01 16:10:04        18.2472
4 2015-01-01 17:09:07        18.1335

import logging
import sys

logging.basicConfig(format='%(asctime)s | %(levelname)s : %(message)s',
                     level=logging.INFO, stream=sys.stdout)

In [5]:
# QC configuration
# For sea water temperature in degrees C
# This configuration is used to call the corresponding method in the ioos_qc library
# See documentation for description of each test and its inputs:
#   https://ioos.github.io/ioos_qc/api/ioos_qc.html#module-ioos_qc.qartod
qc_config = {
    'qartod': {
      "gross_range_test": {
        "fail_span": [10,25],
        "suspect_span": [10,22]
      },
      "flat_line_test": {
        "tolerance": 0.001,
        "suspect_threshold": 10800, #3 hours
        "fail_threshold": 21600     #6 hours - semi diurnal changes
      },
      "rate_of_change_test": {
        "threshold": 0.001
      },
      "spike_test": {
        "suspect_threshold": 0.8,
        "fail_threshold": 3
      },
      "aggregate": {}
    }
}

In [6]:
# Run QC
qc = QcConfig(qc_config)
qc_results =  qc.run(
    inp=data[measurementName],
    tinp=data['timestamp'].values 
)

#qc_results

In [7]:
#NEMS tests

#import Qartod flags
qFlags = qartod.QartodFlags()
"""qFlags.GOOD, qFlags.FAIL, qFlags.SUSPECT"""

##data gap
timeLimit_NEMS = 120 #minutes

timDiff = list(map(operator.sub, timeList[1:],timeList[:-1]))

samplingMask = np.insert(np.array([qFlags.FAIL if x>=np.timedelta64(timeLimit_NEMS,'m') else qFlags.GOOD for x in timDiff]), 0, 1, axis=0) #prepend for start to be true
#print(samplingMask)
qc_results['qartod']['NEMS_gapData'] = ma.masked_array(samplingMask)
#qc_results

title = 'NEMS_gapData' +" - HawQi HBRC"
plot_results(data, measurementName, qc_results, title, 'NEMS_gapData')

In [8]:
title = measurementName +" - HawQi HBRC"

plot_results(data, measurementName, qc_results, title, 'gross_range_test')

In [9]:
plot_results(data, measurementName, qc_results, title, 'flat_line_test')

In [10]:
plot_results(data, measurementName, qc_results, title, 'rate_of_change_test')

In [11]:
plot_results(data, measurementName, qc_results, title, 'spike_test')

In [12]:
# QC Aggregate flag
plot_results(data, measurementName, qc_results, title, 'aggregate')